# 移流方程式

3年16組52番 宮崎弘康

# 1 導入
移流とは、運動量や温度などの物理量が空間内で物質の移動などにより伝わる現象である。  
移流を表す偏微分方程式を移流方程式といい、$u$を物理量、$t$を時間、$x$を位置としたとき
$$\frac{\partial u}{\partial t}+c\frac{\partial u}{\partial x}=0$$
という形で表される。  
このレポートでは、この方程式を、領域の左端と右端が繋がっているとみなした周期的境界条件のもとで数値的に解き、シミュレーションを行う。また、数値計算により得られた結果と解析的に解いた結果と比較する。

# 2 移流方程式の数値計算
移流方程式を数値的に解くとき、どの数値微分法が適しているかをまず検証したい。前進差分、中心差分、後退差分を検証の対象とする。  

## 2.1 前進差分
前進差分の場合、以下の式を用いて近似する。
\begin{align}
  \frac{\partial u}{\partial t} & \sim \frac{u(x_{n+1},t_m)-u(x_n,t_m)}{\Delta t}\\
  \frac{\partial u}{\partial t} & \sim \frac{u(x_n, t_{m+1})-u(x_n,t_m)}{\Delta x}
\end{align}
前進差分を用いて解いた結果は以下のようである。

In [1]:
import numpy as np
from scipy.integrate import solve_ivp
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib import animation, rc


# パラメータ設定
L = 10.0  # 計算領域の長さ
Nx = 101  # 空間方向の格子点数
c = 1.0   # 移流速度
dt = 0.1 # 時間刻み
t_span = [0, 10.0] # 計算終了時間

# 空間離散化
dx = L / Nx
x = np.linspace(0, L, Nx)
t_eval = np.linspace(t_span[0], t_span[1], num = int((t_span[1] - t_span[0]) / dt) + 1)

# 移流方程式の前進差分による計算
def forward_difference(t, u):
    dudx = np.zeros_like(u)
    dudx[:-1] = (u[1:]-u[:-1])/dx
    dudx[-1] = dudx[0]
    return -c * dudx

u0 = np.sin(x * np.pi/5)+1

# Solve the ODEs using solve_ivp
solution = solve_ivp(forward_difference, t_span, u0, t_eval=t_eval)

df = pd.DataFrame(solution.y.T, index=solution.t, columns=x)

# データの再構成
df_melted = df.reset_index().melt(id_vars='index')
df_melted.columns = ['Time', 'X_Coordinate', 'Y_Coordinate']

# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()

ax.set_xlim(( 0, 10))
ax.set_ylim((-0.5, 2.5))

line, = ax.plot([], [], lw=2)

# initialization function: plot the background of each frame
def init():
    line.set_data([], [])
    return (line,)

def animate(frame):
    line.set_data(x, df.iloc[frame])
    return (line,)


anim = animation.FuncAnimation(fig, animate, init_func=init,
                            frames=100, interval=100, blit=True)
rc('animation', html='jshtml')
anim

前進差分では時間$t$が少し進むと発散してしまった。そのため、前進差分は適していないと考えられる。

## 2.2 中心差分
中心差分の場合、以下の式を用いて近似する。
\begin{align}
  \frac{\partial u}{\partial t} & \sim \frac{u(x_{n+1},t_m)-u(x_n,t_m)}{\Delta t}\\
  \frac{\partial u}{\partial t} & \sim \frac{u(x_n, t_{m+1})-u(x_n,t_m)}{\Delta x}
\end{align}
中心差分を用いて解いた結果は以下のようになる。

In [ ]:
# パラメータ設定
L = 10.0  # 計算領域の長さ
Nx = 101  # 空間方向の格子点数
c = 1.0   # 移流速度
dt = 0.1 # 時間刻み
t_span = [0, 50.0] # 計算終了時間

# 空間離散化
dx = L / Nx
x = np.linspace(0, L, Nx)
t_eval = np.linspace(t_span[0], t_span[1], num = int((t_span[1] - t_span[0]) / dt) + 1)

# 移流方程式の中心差分による計算
def center_difference(t, u):
    dudx = np.zeros_like(u)
    dudx[1:-1] = (u[2:]-u[:-2])/dx
    dudx[0] = dudx[-1] = (u[1]-u[-2])/dx
    return -c * dudx

u0 = np.sin(x * np.pi/5)+1

# Solve the ODEs using solve_ivp
solution = solve_ivp(center_difference, t_span, u0, t_eval=t_eval)

df = pd.DataFrame(solution.y.T, index=solution.t, columns=x)

# データの再構成
df_melted = df.reset_index().melt(id_vars='index')
df_melted.columns = ['Time', 'X_Coordinate', 'Y_Coordinate']

# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()

ax.set_xlim(( 0, 10))
ax.set_ylim((-0.5, 2.5))

line, = ax.plot([], [], lw=2)

# initialization function: plot the background of each frame
def init():
    line.set_data([], [])
    return (line,)

def animate(frame):
    line.set_data(x, df.iloc[frame])
    return (line,)


anim = animation.FuncAnimation(fig, animate, init_func=init,
                            frames=500, interval=100, blit=True)
rc('animation', html='jshtml')
anim

中心差分では、時間$t$が進むと「うねり」のようなものが発生してしまい波の形が変わってしまったため、移流方程式を表すものとしては適していないと考えられる。

## 2.3 後退差分
後退差分の場合、以下の式を用いて近似する。
\begin{align}
  \frac{\partial u}{\partial t} & \sim \frac{u(x_n,t_m)-u(x_{n-1},t_m)}{\Delta t}\\
  \frac{\partial u}{\partial t} & \sim \frac{u(x_n, t_{m+1})-u(x_n,t_m)}{\Delta x}
\end{align}
後退差分を用いて解いた結果は以下のようになる。

In [ ]:
# パラメータ設定
L = 10.0  # 計算領域の長さ
Nx = 101  # 空間方向の格子点数
c = 1.0   # 移流速度
dt = 0.1 # 時間刻み
t_span = [0, 50.0] # 計算終了時間

# 空間離散化
dx = L / Nx
x = np.linspace(0, L, Nx)
t_eval = np.linspace(t_span[0], t_span[1], num = int((t_span[1] - t_span[0]) / dt) + 1)

# 移流方程式の後退差分による計算
def backward_difference(t, u):
    dudx = np.zeros_like(u)
    dudx[1:] = (u[1:]-u[:-1])/dx
    dudx[0] = dudx[-1]
    return -c * dudx

u0 = np.sin(x * np.pi/5)+1

# Solve the ODEs using solve_ivp
solution = solve_ivp(backward_difference, t_span, u0, t_eval=t_eval)

df = pd.DataFrame(solution.y.T, index=solution.t, columns=x)

# データの再構成
df_melted = df.reset_index().melt(id_vars='index')
df_melted.columns = ['Time', 'X_Coordinate', 'Y_Coordinate']

# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()

ax.set_xlim(( 0, 10))
ax.set_ylim((-0.5, 2.5))

line, = ax.plot([], [], lw=2)

# initialization function: plot the background of each frame
def init():
    line.set_data([], [])
    return (line,)

def animate(frame):
    line.set_data(x, df.iloc[frame])
    return (line,)

anim = animation.FuncAnimation(fig, animate, init_func=init,
                            frames=500, interval=100, blit=True)
rc('animation', html='jshtml')
anim

後進差分では時間$t$が進むにつれて減衰が見られたが、波の形をおおむね保っているため、3つの中で最も適していると考えられる。

In [ ]:
f = open('./movie_1.gif', 'w')
anim.save('./movie_1.gif', writer='pillow')

# 3 解析解との比較
$$ u(x, t) = \sin \left( \frac{\pi}{5}(x-t) \right) + 1 $$
は上の初期条件のもとで移流方程式の解となる。

In [ ]:
# 解析解の計算
y = np.sin(np.pi/5*(x-t_eval[:, None])) + 1

# DataFrameを作成
df = pd.DataFrame(y, index=t_eval, columns=x)

# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()

ax.set_xlim(( 0, 10))
ax.set_ylim((-0.5, 2.5))

line, = ax.plot([], [], lw=2)

# initialization function: plot the background of each frame
def init():
    line.set_data([], [])
    return (line,)

def animate(frame):
    line.set_data(x, df.iloc[frame])
    return (line,)

anim = animation.FuncAnimation(fig, animate, init_func=init,
                            frames=500, interval=100, blit=True)
rc('animation', html='jshtml')
anim

In [ ]:
f = open('./movie_2.gif', 'w')
anim.save('./movie_2.gif', writer='pillow')

以降では、数値計算によって得られた解を数値解、解析的に得られた解を解析解と呼ぶことにする。  
数値解は、初期分布から形は大きく変わらずに速度一定で進むが、解析解と比べると時間$t$が経過するにつれて減衰したことが分かる。  

# 数値微分の改善
計算方法を変えずに数値解を改善するために、$x$の刻み幅を小さくしてみる。

In [ ]:
# パラメータ設定
L = 10.0  # 計算領域の長さ
Nx = 501  # 空間方向の格子点数
c = 1.0   # 移流速度
dt = 0.1 # 時間刻み
t_span = [0, 50.0] # 計算終了時間

# 空間離散化
dx = L / Nx
x = np.linspace(0, L, Nx)
t_eval = np.linspace(t_span[0], t_span[1], num = int((t_span[1] - t_span[0]) / dt) + 1)

# 移流方程式の後退差分による計算
def backward_difference(t, u):
    dudx = np.zeros_like(u)
    dudx[1:] = (u[1:]-u[:-1])/dx
    dudx[0] = dudx[-1]
    return -c * dudx

u0 = np.sin(x * np.pi/5)+1

# Solve the ODEs using solve_ivp
solution = solve_ivp(backward_difference, t_span, u0, t_eval=t_eval)

df = pd.DataFrame(solution.y.T, index=solution.t, columns=x)

# データの再構成
df_melted = df.reset_index().melt(id_vars='index')
df_melted.columns = ['Time', 'X_Coordinate', 'Y_Coordinate']

# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()

ax.set_xlim(( 0, 10))
ax.set_ylim((-0.5, 2.5))

line, = ax.plot([], [], lw=2)

# initialization function: plot the background of each frame
def init():
    line.set_data([], [])
    return (line,)

def animate(frame):
    line.set_data(x, df.iloc[frame])
    return (line,)

anim = animation.FuncAnimation(fig, animate, init_func=init,
                            frames=500, interval=100, blit=True)
rc('animation', html='jshtml')
anim

In [ ]:
f = open('./movie_2.gif', 'w')
anim.save('./movie_2.gif', writer='pillow')

$x$の格子点数を100から500に増やしたところ、明らかに減衰は遅くなった。このように格子点数を増やすことで実際の移流に近づけることができる。